In [1]:
from IPython.display import display, HTML
import pandas as pd
import sqlite3
from sqlite3 import Error

def create_connection(db_file, delete_db=False):
    import os
    if delete_db and os.path.exists(db_file):
        os.remove(db_file)

    conn = None
    try:
        conn = sqlite3.connect(db_file)
        conn.execute("PRAGMA foreign_keys = 1")
    except Error as e:
        print(e)

    return conn


def create_table(conn, create_table_sql, drop_table_name=None):
    
    if drop_table_name: # You can optionally pass drop_table_name to drop the table. 
        try:
            c = conn.cursor()
            c.execute("""DROP TABLE IF EXISTS %s""" % (drop_table_name))
        except Error as e:
            print(e)
    
    try:
        c = conn.cursor()
        c.execute(create_table_sql)
    except Error as e:
        print(e)
        
def execute_sql_statement(sql_statement, conn):
    cur = conn.cursor()
    cur.execute(sql_statement)

    rows = cur.fetchall()

    return rows

conn = create_connection('la_city_crime.db', delete_db=True)

In [2]:
#Read dataset

df = pd.read_csv("Arrest_data.csv")

df = df.dropna()
print(len(df))
print(df.columns)
df['Charge Group Code'].value_counts()

/usr/local/lib/python3.9/site-packages/IPython/core/interactiveshell.py:3457: DtypeWarning: Columns (21,23) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


414390
Index(['Report ID', 'Report Type', 'Arrest Date', 'Time', 'Area ID',
       'Area Name', 'Reporting District', 'Age', 'Sex Code', 'Descent Code',
       'Charge Group Code', 'Charge Group Description', 'Arrest Type Code',
       'Charge', 'Charge Description', 'Disposition Description', 'Address',
       'Cross Street', 'LAT', 'LON', 'Location', 'Booking Date',
       'Booking Time', 'Booking Location', 'Booking Location Code'],
      dtype='object')


16.0    90302
24.0    82146
22.0    66380
23.0    33213
13.0    24266
4.0     20679
8.0     16598
7.0     15495
12.0    14968
3.0     11811
6.0     10531
5.0      7650
10.0     3771
14.0     3169
11.0     3155
9.0      2681
20.0     1909
18.0     1791
15.0     1240
1.0       751
17.0      525
2.0       514
19.0      279
26.0      202
21.0      190
25.0      133
27.0       41
Name: Charge Group Code, dtype: int64

In [60]:
sql_charge_detals = "CREATE TABLE ChargeDetails(ChargeGroupCode INTEGER NOT NULL PRIMARY KEY, ChargeGroupDesc TEXT NOT NULL, Charge TEXT NOT NULL, ChargeDesc TEXT NOT NULL, ChargeCount INTEGER NOT NULL);"

create_table(conn, sql_charge_detals, drop_table_name='ChargeDetails')

rows = []
charge_group_code = []
charge_group_desc = []
charge_code = []
charge_desc = []
charge_count = {}
df_charge_data = df[['Charge Group Code', 'Charge Group Description', 'Charge', 'Charge Description']]
print(df_charge_data.head(), len(df_charge_data), df_charge_data.index)

count = 0
for i in df_charge_data.index[0:10000]:
    count+=1
    try:
        charge_count[int(df_charge_data['Charge Group Code'][i])] +=1
    except KeyError:
        charge_count[int(df_charge_data['Charge Group Code'][i])] = 1
    if(int(df_charge_data['Charge Group Code'][i]) not in charge_group_code):
        charge_group_code += [int(df_charge_data['Charge Group Code'][i])]
        charge_group_desc += [df_charge_data['Charge Group Description'][i]]
        charge_code += [df_charge_data['Charge'][i] + ":"]
        charge_desc += [df_charge_data['Charge Description'][i] + ":"]

    else:
        index = charge_group_code.index(int(df_charge_data['Charge Group Code'][i]))
        if(df_charge_data['Charge'][i] not in charge_code[index]):
            charge_code[index] += df_charge_data['Charge'][i] + ":"
            charge_desc[index] += df_charge_data['Charge Description'][i] + ":"

print(charge_count)
    
for i in range(0, len(charge_group_code)):
    rows += [(int(charge_group_code[i]), charge_group_desc[i], charge_code[i][0:-1], charge_desc[i][0:-1],charge_count[int(charge_group_code[i])],)]

print(charge_group_code)
    
#print(len(charge_group_code), len(list(set(charge_group_code))))
#print(rows)
sql = """INSERT INTO ChargeDetails VALUES (?,?,?,?,?);"""
cur = conn.cursor()
cur.executemany(sql, rows)

conn.commit()
print(count)


      Charge Group Code Charge Group Description       Charge  \
331                 5.0                 Burglary        459PC   
673                 6.0                  Larceny        666PC   
784                 5.0                 Burglary        459PC   
2256               10.0       Fraud/Embezzlement  10980(C)2WI   
3108                7.0            Vehicle Theft   10851(A)VC   

                             Charge Description  
331                                    BURGLARY  
673    PETTY THEFT W/SPECIFIED PRIOR CONVICTION  
784                                    BURGLARY  
2256  OBTAIN/ETC AID BY FALSE STMENT/ETC > $400  
3108           TAKE VEHICLE W/O OWNER'S CONSENT   414390 Int64Index([    331,     673,     784,    2256,    3108,    4675,    4693,
               4922,    5175,   44678,
            ...
            1322791, 1322792, 1322793, 1322795, 1322798, 1322805, 1322808,
            1322814, 1322817, 1322819],
           dtype='int64', length=414390)
{5: 145, 6: 204,

In [61]:
import plotly.graph_objects as go

charge_by_group_count_data = execute_sql_statement("SELECT ChargeGroupDesc, ChargeCount FROM ChargeDetails ORDER BY ChargeCount DESC", conn)

charges = [row[0] for row in charge_by_group_count_data]
counts = [row[1] for row in charge_by_group_count_data]

fig = go.Figure([go.Bar(x=charges, y=counts,text=counts,
            textposition='auto')])
fig.update_layout(title_text='Commonly Committed Crimes In LA City')
fig.show()

fig = go.Figure(data=[go.Pie(labels=charges, values=counts)])
fig.show()



# Inferences From The Above Graphs

## 5 Most Commonly Committed Crimes
1) Narcotic Drug Laws

2) Miscellaneous Other Violations

3) Driving Under Influence

4) Moving Traffic Violations

5) Prostitution/Allied

## The top 3 crimes account for over 50% of the crimes in LA City
## The top 5 crimes account for over 70% of the crimes in LA City

In [65]:
sql_location_details = "CREATE TABLE LocationDetails(AreaID INTEGER NOT NULL PRIMARY KEY, AreaName TEXT NOT NULL, ReportingDistrict TEXT NOT NULL, Address TEXT NOT NULL, CrossStreet TEXT NOT NULL, Location TEXT NOT NULL);"

create_table(conn, sql_location_details, drop_table_name='LocationDetails')

rows = []
area_id = []
area_name = []
reporting_district = []
address = []
cross_street = []
location = []
df_area_data = df[['Area ID', 'Area Name', 'Reporting District', 'Address', 'Cross Street', 'Location']]

for i in df_area_data.index:
    #print(i)
    if(int(df_area_data['Area ID'][i]) not in area_id):
        area_id += [int(df_area_data['Area ID'][i])]
        area_name += [df_area_data['Area Name'][i]]
        reporting_district += [str(df_area_data['Reporting District'][i]) + ":"]
        address += [str(df_area_data['Address'][i].replace(" ",'')) + ":"]
        cross_street += [df_area_data['Cross Street'][i].replace(" ",'') + ":"]
        location += [df_area_data['Location'][i].replace(" ",'') + ":"]
        

    else:
        index = area_id.index(int(df_area_data['Area ID'][i]))
        if(str(df_area_data['Reporting District'][i]) not in reporting_district[index]):
            reporting_district[index] += str(df_area_data['Reporting District'][i]) + ":"
        if(df_area_data['Address'][i].replace(" ",'') not in address[index]):
            address[index] += str(df_area_data['Address'][i].replace(" ",'')) + ":"
            cross_street[index] += df_area_data['Cross Street'][i].replace(" ",'') + ":"
            location[index] += df_area_data['Location'][i].replace(" ",'') + ":"

print(len(area_id), len(address), len(reporting_district), len(location), len(cross_street), len(area_name))

for i in range(0, len(area_id)):
    rows += [(int(area_id[i]), area_name[i], reporting_district[i][0:-1], address[i][0:-1], cross_street[i][0:-1], location[i][0:-1],)]

print(rows[0])
    
sql = """INSERT INTO LocationDetails VALUES (?,?,?,?,?,?);"""
cur = conn.cursor()
cur.executemany(sql, rows)

conn.commit()


331
673
784
2256
3108
4675
4693
4922
5175
44678
44680
237483
243568
258282
296395
301913
301915
311603
312275
327164
327165
327166
328562
341161
349271
360796
362820
364103
366425
366426
378642
378644
378645
378649
378650
378653
378655
378656
378658
378659
378660
378661
378662
378664
378665
378667
378668
378670
378671
378673
378676
378680
378681
378682
378683
378684
378686
378687
378690
378691
378695
378696
378698
378699
378700
378704
378706
378708
378709
378716
378719
378720
378721
378723
378726
378731
378737
378738
378739
378741
378742
378746
378747
378748
378753
378755
378756
378757
378761
378769
378772
378773
378775
378782
378783
378789
378791
378795
378796
378797
378800
378801
378802
378803
378804
378806
378807
378810
378812
378815
378816
378821
378826
378827
378829
378830
378832
378833
378836
378838
378839
378840
378842
378844
378845
378846
378847
378850
378853
378855
378858
378859
378863
378864
378866
378871
378872
378882
378887
378890
378892
378894
378899
378900
378906
378907
3

In [70]:
import plotly.graph_objects as go

area_data = execute_sql_statement("SELECT * FROM LocationDetails ORDER BY AreaID ASC", conn)

area_name = [row[1] for row in area_data]
area_rep_district = [len(row[2].split(":")) for row in area_data]

fig = go.Figure([go.Bar(x=area_id, y=area_rep_district,text=area_rep_district,
            textposition='auto')])
fig.update_layout(title_text='Areawise reporting districts')
fig.show()

fig = go.Figure(data=[go.Pie(labels=area_name, values=area_rep_district)])
fig.show()

In [ ]:


sql_arrest = '''create table ArrestDetails(ReportID INTEGER NOT NULL PRIMARY KEY, 
                                        ReportType TEXT NOT NULL, 
                                        ArrestDate TEXT NOT NULL,
                                        ArrestTime INTEGER NOT NULL, 
                                        ArrestTypeCode TEXT NOT NULL,
                                        Age INTEGER NOT NULL,
                                        SexCode TEXT NOT NULL,
                                        DescentCode TEXT NOT NULL,
                                        AreaID INTEGER NOT NULL,
                                        ChargeGroupCode INTEGER NOT NULL,
                                        FOREIGN KEY (AreaID) REFERENCES LocationDetails(AreaID),
                                        FOREIGN KEY (ChargeGroupCode) REFERENCES ChargeDetails(ChargeGroupCode)
                                        );
'''
create_table(conn, sql_arrest)

sql_st = """INSERT INTO ArrestDetails VALUES (?,?,?,?,?,?,?,?,?,?);"""

records = [(45,"RFC","12-11-2021",21,"FD",22,"M","AS",1,1)]
cur = conn.cursor()
cur.executemany(sql_st, records)

In [ ]:
execute_sql_statement("SELECT * FROM ArrestDetails;", conn)

[(45, 'RFC', '12-11-2021', 21, 'FD', 22, 'M', 'AS', 1, 1)]